In [1]:
import logging
logger = logging.getLogger()
logger.setLevel(logging.DEBUG)
logging.debug('Needed to run for Jupyter Notebook')

DEBUG:root:Needed to run for Jupyter Notebook


In [2]:
import acme

In [3]:
environment_library = 'gym'

In [4]:
import IPython

from acme import environment_loop
from acme import specs
from acme import wrappers
from acme.agents.tf import d4pg
from acme.tf import networks
from acme.tf import utils as tf2_utils
from acme.utils import loggers
import numpy as np
import sonnet as snt

from absl import app
from absl import flags
import acme
from acme.agents.tf import dqn
from acme.tf import networks

# Import the selected environment lib
if environment_library == 'dm_control':
  from dm_control import suite
elif environment_library == 'gym':
  import gym

# Imports required for visualization
import pyvirtualdisplay
import imageio
import base64

# Set up a virtual display for rendering.
display = pyvirtualdisplay.Display(visible=0, size=(1400, 900)).start()

DEBUG:matplotlib:matplotlib data path: /home/hayato/anaconda3/envs/acme/lib/python3.8/site-packages/matplotlib/mpl-data
DEBUG:matplotlib:CONFIGDIR=/home/hayato/.config/matplotlib
DEBUG:matplotlib:matplotlib version 3.4.2
DEBUG:matplotlib:interactive is False
DEBUG:matplotlib:platform is linux
DEBUG:matplotlib:loaded modules: ['sys', 'builtins', '_frozen_importlib', '_imp', '_warnings', '_io', 'marshal', 'posix', '_frozen_importlib_external', '_thread', '_weakref', 'time', 'zipimport', '_codecs', 'codecs', 'encodings.aliases', 'encodings', 'encodings.utf_8', '_signal', '__main__', 'encodings.latin_1', '_abc', 'abc', 'io', '_stat', 'stat', '_collections_abc', 'genericpath', 'posixpath', 'os.path', 'os', '_sitebuiltins', '_locale', '_bootlocale', 'types', 'importlib._bootstrap', 'importlib._bootstrap_external', 'warnings', 'importlib', 'importlib.machinery', 'importlib.abc', '_operator', 'operator', 'keyword', '_heapq', 'heapq', 'itertools', 'reprlib', '_collections', 'collections', '_fun

DEBUG:matplotlib:CACHEDIR=/home/hayato/.cache/matplotlib
DEBUG:matplotlib.font_manager:Using fontManager instance from /home/hayato/.cache/matplotlib/fontlist-v330.json
DEBUG:matplotlib.pyplot:Loaded backend agg version unknown.
DEBUG:tensorflow:Falling back to TensorFlow client; we recommended you install the Cloud TPU client directly with pip install cloud-tpu-client.
DEBUG:h5py._conv:Creating converter from 7 to 5
DEBUG:h5py._conv:Creating converter from 5 to 7
DEBUG:h5py._conv:Creating converter from 7 to 5
DEBUG:h5py._conv:Creating converter from 5 to 7
DEBUG:easyprocess:version=0.3
DEBUG:pyvirtualdisplay:version=2.2
DEBUG:easyprocess:command: ['Xvfb', '-help']
DEBUG:easyprocess:process was started (pid=52384)
DEBUG:easyprocess:process has ended, return code=0
DEBUG:pyvirtualdisplay.abstractdisplay:command: ['Xvfb', '-br', '-nolisten', 'tcp', '-screen', '0', '1400x900x24', '-displayfd', '46']
DEBUG:pyvirtualdisplay.abstractdisplay:set $DISPLAY=:2


In [5]:
# helper functions
import functools

from acme import wrappers
import dm_env
import gym

def make_environment(level: str, evaluation: bool = False) -> dm_env.Environment:
  env = gym.make(level, full_action_space=True)

  max_episode_len = 108_000 if evaluation else 50_000

  return wrappers.wrap_all(env, [
      wrappers.GymAtariAdapter,
      functools.partial(
          wrappers.AtariWrapper,
          to_float=True,
          max_episode_len=max_episode_len,
          zero_discount_on_life_loss=True,
      ),
      wrappers.SinglePrecisionWrapper,
  ])

In [6]:
# Create a simple helper function to render a frame from the current state of
# the environment.
def render(env):
    return env.environment.render(mode='rgb_array')

def display_video(frames, filename='temp.mp4'):
  """Save and display video."""

  # Write video
  with imageio.get_writer(filename, fps=60) as video:
    for frame in frames:
      video.append_data(frame)

  # Read video and display the video
  video = open(filename, 'rb').read()
  b64_video = base64.b64encode(video)
  video_tag = ('<video  width="320" height="240" controls alt="test" '
               'src="data:video/mp4;base64,{0}">').format(b64_video.decode())

  return IPython.display.HTML(video_tag)

In [7]:
environment = make_environment('BreakoutDeterministic-v4')
environment_spec = acme.make_environment_spec(environment)
network = networks.DQNAtariNetwork(environment_spec.actions.num_values)

# Create a logger for the agent and environment loop.
# agent_logger = loggers.TerminalLogger(label='agent')
env_loop_logger = loggers.TerminalLogger(label='env_loop')

# agent = dqn.DQN(environment_spec, network, logger=agent_logger)
agent = dqn.DQN(environment_spec, network)

# Create an loop connecting this agent to the environment created above.
env_loop = acme.EnvironmentLoop(
    environment, agent, logger=env_loop_logger)
# env_loop = acme.EnvironmentLoop(environment, agent)

# Run a `num_episodes` training episodes.
# Rerun this cell until the agent has learned the given task.
# env_loop.run(num_episodes=1000)

INFO:absl:Attempting to restore checkpoint: None


In [ ]:
# Run a `num_episodes` training episodes.
# Rerun this cell until the agent has learned the given task.
env_loop.run(num_episodes=5000)

INFO:root:[Learner] Loss = 0.194 | Steps = 1992508 | Walltime = 264683.772
INFO:root:[Learner] Loss = 0.345 | Steps = 1992517 | Walltime = 264684.884
INFO:root:[Learner] Loss = 0.157 | Steps = 1992525 | Walltime = 264685.956
INFO:root:[Learner] Loss = 0.281 | Steps = 1992533 | Walltime = 264687.064
INFO:root:[Learner] Loss = 0.245 | Steps = 1992541 | Walltime = 264688.138
INFO:root:[Learner] Loss = 0.230 | Steps = 1992549 | Walltime = 264689.213
INFO:root:[Env Loop] Episode Length = 385 | Episode Return = 27.0 | Episodes = 60001 | Steps = 15941436 | Steps Per Second = 59.757
INFO:root:[Learner] Loss = 0.195 | Steps = 1992556 | Walltime = 264690.224
INFO:root:[Learner] Loss = 0.269 | Steps = 1992564 | Walltime = 264691.267
INFO:root:[Learner] Loss = 0.361 | Steps = 1992572 | Walltime = 264692.297
INFO:root:[Learner] Loss = 0.228 | Steps = 1992580 | Walltime = 264693.328
INFO:root:[Learner] Loss = 0.321 | Steps = 1992589 | Walltime = 264694.433
INFO:root:[Learner] Loss = 0.317 | Steps = 

INFO:root:[Env Loop] Episode Length = 376 | Episode Return = 37.0 | Episodes = 60014 | Steps = 15946727 | Steps Per Second = 63.943
INFO:root:[Learner] Loss = 0.332 | Steps = 1993217 | Walltime = 264776.005
INFO:root:[Learner] Loss = 0.161 | Steps = 1993225 | Walltime = 264777.060
INFO:root:[Learner] Loss = 0.238 | Steps = 1993233 | Walltime = 264778.065
INFO:root:[Learner] Loss = 0.287 | Steps = 1993241 | Walltime = 264779.070
INFO:root:[Learner] Loss = 0.211 | Steps = 1993249 | Walltime = 264780.116
INFO:root:[Learner] Loss = 0.291 | Steps = 1993257 | Walltime = 264781.124
INFO:root:[Env Loop] Episode Length = 321 | Episode Return = 50.0 | Episodes = 60015 | Steps = 15947048 | Steps Per Second = 61.895
INFO:root:[Learner] Loss = 0.273 | Steps = 1993265 | Walltime = 264782.199
INFO:root:[Learner] Loss = 0.253 | Steps = 1993273 | Walltime = 264783.219
INFO:root:[Learner] Loss = 0.274 | Steps = 1993281 | Walltime = 264784.233
INFO:root:[Learner] Loss = 0.282 | Steps = 1993290 | Walltime

INFO:root:[Learner] Loss = 0.321 | Steps = 1993880 | Walltime = 264862.972
INFO:root:[Learner] Loss = 0.274 | Steps = 1993888 | Walltime = 264863.980
INFO:root:[Learner] Loss = 0.216 | Steps = 1993896 | Walltime = 264865.025
INFO:root:[Learner] Loss = 0.286 | Steps = 1993904 | Walltime = 264866.033
INFO:root:[Learner] Loss = 0.240 | Steps = 1993912 | Walltime = 264867.107
INFO:root:[Learner] Loss = 0.316 | Steps = 1993920 | Walltime = 264868.140
INFO:root:[Learner] Loss = 0.302 | Steps = 1993928 | Walltime = 264869.175
INFO:root:[Env Loop] Episode Length = 441 | Episode Return = 47.0 | Episodes = 60029 | Steps = 15952466 | Steps Per Second = 61.812
INFO:root:[Learner] Loss = 0.372 | Steps = 1993936 | Walltime = 264870.215
INFO:root:[Learner] Loss = 0.342 | Steps = 1993944 | Walltime = 264871.257
INFO:root:[Learner] Loss = 0.381 | Steps = 1993952 | Walltime = 264872.298
INFO:root:[Learner] Loss = 0.316 | Steps = 1993960 | Walltime = 264873.320
INFO:root:[Learner] Loss = 0.313 | Steps = 

INFO:root:[Learner] Loss = 0.288 | Steps = 1994565 | Walltime = 264952.188
INFO:root:[Learner] Loss = 0.254 | Steps = 1994572 | Walltime = 264953.242
INFO:root:[Learner] Loss = 0.263 | Steps = 1994579 | Walltime = 264954.289
INFO:root:[Env Loop] Episode Length = 351 | Episode Return = 40.0 | Episodes = 60043 | Steps = 15957662 | Steps Per Second = 57.043
INFO:root:[Learner] Loss = 0.230 | Steps = 1994585 | Walltime = 264955.310
INFO:root:[Learner] Loss = 0.229 | Steps = 1994592 | Walltime = 264956.335
INFO:root:[Learner] Loss = 0.285 | Steps = 1994599 | Walltime = 264957.409
INFO:root:[Learner] Loss = 0.223 | Steps = 1994606 | Walltime = 264958.434
INFO:root:[Learner] Loss = 0.300 | Steps = 1994614 | Walltime = 264959.463
INFO:root:[Learner] Loss = 0.220 | Steps = 1994622 | Walltime = 264960.500
INFO:root:[Learner] Loss = 0.233 | Steps = 1994630 | Walltime = 264961.502
INFO:root:[Env Loop] Episode Length = 434 | Episode Return = 37.0 | Episodes = 60044 | Steps = 15958096 | Steps Per Se

INFO:root:[Learner] Loss = 0.290 | Steps = 1995233 | Walltime = 265038.901
INFO:root:[Learner] Loss = 0.230 | Steps = 1995241 | Walltime = 265039.923
INFO:root:[Env Loop] Episode Length = 270 | Episode Return = 34.0 | Episodes = 60058 | Steps = 15962967 | Steps Per Second = 63.586
INFO:root:[Learner] Loss = 0.269 | Steps = 1995249 | Walltime = 265040.944
INFO:root:[Learner] Loss = 0.333 | Steps = 1995257 | Walltime = 265041.993
INFO:root:[Learner] Loss = 0.334 | Steps = 1995265 | Walltime = 265043.078
INFO:root:[Learner] Loss = 0.331 | Steps = 1995273 | Walltime = 265044.098
INFO:root:[Env Loop] Episode Length = 238 | Episode Return = 28.0 | Episodes = 60059 | Steps = 15963205 | Steps Per Second = 60.114
INFO:root:[Learner] Loss = 0.168 | Steps = 1995281 | Walltime = 265045.209
INFO:root:[Learner] Loss = 0.363 | Steps = 1995289 | Walltime = 265046.212
INFO:root:[Learner] Loss = 0.188 | Steps = 1995297 | Walltime = 265047.212
INFO:root:[Learner] Loss = 0.248 | Steps = 1995306 | Walltime

...

INFO:root:[Learner] Loss = 0.358 | Steps = 2089956 | Walltime = 277453.513
INFO:root:[Learner] Loss = 0.171 | Steps = 2089964 | Walltime = 277454.675
INFO:root:[Learner] Loss = 0.200 | Steps = 2089972 | Walltime = 277455.758
INFO:root:[Learner] Loss = 0.364 | Steps = 2089980 | Walltime = 277456.838
INFO:root:[Learner] Loss = 0.239 | Steps = 2089988 | Walltime = 277457.885
INFO:root:[Env Loop] Episode Length = 379 | Episode Return = 60.0 | Episodes = 62622 | Steps = 16720958 | Steps Per Second = 57.504
INFO:root:[Learner] Loss = 0.208 | Steps = 2089996 | Walltime = 277458.989
INFO:root:[Learner] Loss = 0.220 | Steps = 2090004 | Walltime = 277460.094
INFO:root:[Learner] Loss = 0.258 | Steps = 2090012 | Walltime = 277461.190
INFO:root:[Learner] Loss = 0.265 | Steps = 2090019 | Walltime = 277462.214
INFO:root:[Learner] Loss = 0.123 | Steps = 2090027 | Walltime = 277463.337
INFO:root:[Env Loop] Episode Length = 283 | Episode Return = 40.0 | Episodes = 62623 | Steps = 16721241 | Steps Per Se

INFO:root:[Learner] Loss = 0.228 | Steps = 2090542 | Walltime = 277543.307
INFO:root:[Learner] Loss = 0.283 | Steps = 2090549 | Walltime = 277544.437
INFO:root:[Learner] Loss = 0.319 | Steps = 2090556 | Walltime = 277545.551
INFO:root:[Env Loop] Episode Length = 259 | Episode Return = 44.0 | Episodes = 62637 | Steps = 16725446 | Steps Per Second = 50.692
INFO:root:[Learner] Loss = 0.347 | Steps = 2090562 | Walltime = 277546.666
INFO:root:[Learner] Loss = 0.370 | Steps = 2090568 | Walltime = 277547.756
INFO:root:[Learner] Loss = 0.264 | Steps = 2090574 | Walltime = 277548.990
INFO:root:[Learner] Loss = 0.292 | Steps = 2090579 | Walltime = 277550.001
INFO:root:[Learner] Loss = 0.256 | Steps = 2090586 | Walltime = 277551.082
INFO:root:[Learner] Loss = 0.220 | Steps = 2090592 | Walltime = 277552.245
INFO:root:[Env Loop] Episode Length = 315 | Episode Return = 46.0 | Episodes = 62638 | Steps = 16725761 | Steps Per Second = 42.782
INFO:root:[Learner] Loss = 0.229 | Steps = 2090597 | Walltime

INFO:root:[Learner] Loss = 0.353 | Steps = 2091118 | Walltime = 277629.961
INFO:root:[Learner] Loss = 0.215 | Steps = 2091126 | Walltime = 277631.088
INFO:root:[Learner] Loss = 0.207 | Steps = 2091133 | Walltime = 277632.092
INFO:root:[Learner] Loss = 0.270 | Steps = 2091141 | Walltime = 277633.163
INFO:root:[Learner] Loss = 0.229 | Steps = 2091148 | Walltime = 277634.173
INFO:root:[Env Loop] Episode Length = 388 | Episode Return = 43.0 | Episodes = 62654 | Steps = 16730212 | Steps Per Second = 57.061
INFO:root:[Learner] Loss = 0.238 | Steps = 2091155 | Walltime = 277635.183
INFO:root:[Learner] Loss = 0.238 | Steps = 2091163 | Walltime = 277636.305
INFO:root:[Learner] Loss = 0.179 | Steps = 2091170 | Walltime = 277637.345
INFO:root:[Learner] Loss = 0.330 | Steps = 2091178 | Walltime = 277638.460
INFO:root:[Env Loop] Episode Length = 237 | Episode Return = 29.0 | Episodes = 62655 | Steps = 16730449 | Steps Per Second = 55.743
INFO:root:[Learner] Loss = 0.294 | Steps = 2091185 | Walltime

INFO:root:[Learner] Loss = 0.327 | Steps = 2091665 | Walltime = 277718.622
INFO:root:[Env Loop] Episode Length = 339 | Episode Return = 40.0 | Episodes = 62669 | Steps = 16734348 | Steps Per Second = 51.696
INFO:root:[Learner] Loss = 0.240 | Steps = 2091672 | Walltime = 277719.741
INFO:root:[Learner] Loss = 0.245 | Steps = 2091680 | Walltime = 277720.854
INFO:root:[Learner] Loss = 0.343 | Steps = 2091688 | Walltime = 277721.956
INFO:root:[Learner] Loss = 0.193 | Steps = 2091695 | Walltime = 277723.099
INFO:root:[Learner] Loss = 0.303 | Steps = 2091702 | Walltime = 277724.169
INFO:root:[Env Loop] Episode Length = 313 | Episode Return = 42.0 | Episodes = 62670 | Steps = 16734661 | Steps Per Second = 53.716
INFO:root:[Learner] Loss = 0.235 | Steps = 2091709 | Walltime = 277725.185
INFO:root:[Learner] Loss = 0.209 | Steps = 2091716 | Walltime = 277726.255
INFO:root:[Learner] Loss = 0.207 | Steps = 2091724 | Walltime = 277727.404
INFO:root:[Learner] Loss = 0.278 | Steps = 2091732 | Walltime

INFO:root:[Learner] Loss = 0.133 | Steps = 2092252 | Walltime = 277806.294
INFO:root:[Learner] Loss = 0.288 | Steps = 2092259 | Walltime = 277807.350
INFO:root:[Learner] Loss = 0.300 | Steps = 2092267 | Walltime = 277808.428
INFO:root:[Learner] Loss = 0.316 | Steps = 2092274 | Walltime = 277809.461
INFO:root:[Learner] Loss = 0.224 | Steps = 2092281 | Walltime = 277810.598
INFO:root:[Learner] Loss = 0.266 | Steps = 2092288 | Walltime = 277811.710
INFO:root:[Env Loop] Episode Length = 317 | Episode Return = 43.0 | Episodes = 62685 | Steps = 16739311 | Steps Per Second = 53.222
INFO:root:[Learner] Loss = 0.256 | Steps = 2092295 | Walltime = 277812.747
INFO:root:[Learner] Loss = 0.267 | Steps = 2092302 | Walltime = 277813.773
INFO:root:[Learner] Loss = 0.283 | Steps = 2092309 | Walltime = 277814.779
INFO:root:[Learner] Loss = 0.361 | Steps = 2092316 | Walltime = 277815.811
INFO:root:[Env Loop] Episode Length = 260 | Episode Return = 37.0 | Episodes = 62686 | Steps = 16739571 | Steps Per Se

In [27]:
timestep = environment.reset()
frames = [render(environment)]

while not timestep.last():
  # Simple environment loop.
  action = agent.select_action(timestep.observation)
  timestep = environment.step(action)

  # Render the scene and add it to the frame stack.
  frames.append(render(environment))

# Save and display a video of the behaviour.
display_video(np.array(frames))

In [25]:
env_loop.run(num_episodes=5000)

INFO:root:[Learner] Loss = 0.203 | Steps = 1632469 | Walltime = 217182.663
INFO:root:[Learner] Loss = 0.204 | Steps = 1632476 | Walltime = 217183.835
INFO:root:[Learner] Loss = 0.251 | Steps = 1632484 | Walltime = 217184.919
INFO:root:[Learner] Loss = 0.273 | Steps = 1632492 | Walltime = 217186.049
INFO:root:[Learner] Loss = 0.311 | Steps = 1632500 | Walltime = 217187.180
INFO:root:[Env Loop] Episode Length = 308 | Episode Return = 46.0 | Episodes = 50001 | Steps = 13061047 | Steps Per Second = 55.220
INFO:root:[Learner] Loss = 0.238 | Steps = 1632507 | Walltime = 217188.220
INFO:root:[Learner] Loss = 0.256 | Steps = 1632515 | Walltime = 217189.347
INFO:root:[Learner] Loss = 0.189 | Steps = 1632523 | Walltime = 217190.367
INFO:root:[Learner] Loss = 0.243 | Steps = 1632531 | Walltime = 217191.402
INFO:root:[Learner] Loss = 0.262 | Steps = 1632539 | Walltime = 217192.483
INFO:root:[Learner] Loss = 0.310 | Steps = 1632547 | Walltime = 217193.495
INFO:root:[Env Loop] Episode Length = 384 |

INFO:root:[Env Loop] Episode Length = 232 | Episode Return = 27.0 | Episodes = 50017 | Steps = 13065877 | Steps Per Second = 62.894
INFO:root:[Learner] Loss = 0.316 | Steps = 1633113 | Walltime = 217270.074
INFO:root:[Learner] Loss = 0.243 | Steps = 1633121 | Walltime = 217271.114
INFO:root:[Learner] Loss = 0.222 | Steps = 1633129 | Walltime = 217272.142
INFO:root:[Env Loop] Episode Length = 175 | Episode Return = 15.0 | Episodes = 50018 | Steps = 13066052 | Steps Per Second = 61.233
INFO:root:[Learner] Loss = 0.326 | Steps = 1633137 | Walltime = 217273.201
INFO:root:[Learner] Loss = 0.382 | Steps = 1633145 | Walltime = 217274.204
INFO:root:[Learner] Loss = 0.262 | Steps = 1633153 | Walltime = 217275.255
INFO:root:[Learner] Loss = 0.265 | Steps = 1633162 | Walltime = 217276.344
INFO:root:[Learner] Loss = 0.353 | Steps = 1633170 | Walltime = 217277.426
INFO:root:[Env Loop] Episode Length = 349 | Episode Return = 79.0 | Episodes = 50019 | Steps = 13066401 | Steps Per Second = 62.035
INFO

INFO:root:[Learner] Loss = 0.252 | Steps = 1633742 | Walltime = 217352.575
INFO:root:[Learner] Loss = 0.359 | Steps = 1633750 | Walltime = 217353.580
INFO:root:[Env Loop] Episode Length = 304 | Episode Return = 51.0 | Episodes = 50035 | Steps = 13071031 | Steps Per Second = 61.688
INFO:root:[Learner] Loss = 0.228 | Steps = 1633758 | Walltime = 217354.642
INFO:root:[Learner] Loss = 0.241 | Steps = 1633766 | Walltime = 217355.680
INFO:root:[Learner] Loss = 0.285 | Steps = 1633774 | Walltime = 217356.698
INFO:root:[Learner] Loss = 0.242 | Steps = 1633782 | Walltime = 217357.735
INFO:root:[Learner] Loss = 0.353 | Steps = 1633790 | Walltime = 217358.778
INFO:root:[Env Loop] Episode Length = 339 | Episode Return = 51.0 | Episodes = 50036 | Steps = 13071370 | Steps Per Second = 61.376
INFO:root:[Learner] Loss = 0.285 | Steps = 1633798 | Walltime = 217359.823
INFO:root:[Learner] Loss = 0.285 | Steps = 1633806 | Walltime = 217360.868
INFO:root:[Learner] Loss = 0.237 | Steps = 1633814 | Walltime

INFO:root:[Learner] Loss = 0.297 | Steps = 1634370 | Walltime = 217434.482
INFO:root:[Learner] Loss = 0.302 | Steps = 1634378 | Walltime = 217435.565
INFO:root:[Learner] Loss = 0.426 | Steps = 1634386 | Walltime = 217436.607
INFO:root:[Env Loop] Episode Length = 366 | Episode Return = 64.0 | Episodes = 50053 | Steps = 13076094 | Steps Per Second = 60.005
INFO:root:[Learner] Loss = 0.335 | Steps = 1634394 | Walltime = 217437.681
INFO:root:[Learner] Loss = 0.249 | Steps = 1634402 | Walltime = 217438.766
INFO:root:[Env Loop] Episode Length = 116 | Episode Return = 9.0 | Episodes = 50054 | Steps = 13076210 | Steps Per Second = 58.107
INFO:root:[Learner] Loss = 0.226 | Steps = 1634410 | Walltime = 217439.842
INFO:root:[Learner] Loss = 0.441 | Steps = 1634418 | Walltime = 217440.912
INFO:root:[Learner] Loss = 0.226 | Steps = 1634426 | Walltime = 217441.996
INFO:root:[Env Loop] Episode Length = 195 | Episode Return = 17.0 | Episodes = 50055 | Steps = 13076405 | Steps Per Second = 59.562
INFO:

INFO:root:[Learner] Loss = 0.237 | Steps = 1634986 | Walltime = 217514.839
INFO:root:[Learner] Loss = 0.154 | Steps = 1634994 | Walltime = 217515.861
INFO:root:[Learner] Loss = 0.196 | Steps = 1635003 | Walltime = 217516.965
INFO:root:[Learner] Loss = 0.300 | Steps = 1635012 | Walltime = 217518.070
INFO:root:[Learner] Loss = 0.214 | Steps = 1635020 | Walltime = 217519.071
INFO:root:[Env Loop] Episode Length = 311 | Episode Return = 42.0 | Episodes = 50072 | Steps = 13081188 | Steps Per Second = 63.840
INFO:root:[Learner] Loss = 0.287 | Steps = 1635028 | Walltime = 217520.099
INFO:root:[Learner] Loss = 0.277 | Steps = 1635036 | Walltime = 217521.103
INFO:root:[Learner] Loss = 0.280 | Steps = 1635044 | Walltime = 217522.133
INFO:root:[Learner] Loss = 0.236 | Steps = 1635052 | Walltime = 217523.167
INFO:root:[Env Loop] Episode Length = 262 | Episode Return = 32.0 | Episodes = 50073 | Steps = 13081450 | Steps Per Second = 62.245
INFO:root:[Learner] Loss = 0.249 | Steps = 1635060 | Walltime

...

INFO:root:[Learner] Loss = 0.265 | Steps = 1807664 | Walltime = 240169.327
INFO:root:[Learner] Loss = 0.230 | Steps = 1807672 | Walltime = 240170.378
INFO:root:[Learner] Loss = 0.210 | Steps = 1807680 | Walltime = 240171.416
INFO:root:[Learner] Loss = 0.296 | Steps = 1807688 | Walltime = 240172.441
INFO:root:[Learner] Loss = 0.254 | Steps = 1807696 | Walltime = 240173.448
INFO:root:[Learner] Loss = 0.238 | Steps = 1807704 | Walltime = 240174.486
INFO:root:[Env Loop] Episode Length = 352 | Episode Return = 62.0 | Episodes = 54925 | Steps = 14462647 | Steps Per Second = 61.693
INFO:root:[Learner] Loss = 0.395 | Steps = 1807712 | Walltime = 240175.589
INFO:root:[Learner] Loss = 0.213 | Steps = 1807721 | Walltime = 240176.715
INFO:root:[Learner] Loss = 0.310 | Steps = 1807729 | Walltime = 240177.795
INFO:root:[Env Loop] Episode Length = 186 | Episode Return = 18.0 | Episodes = 54926 | Steps = 14462833 | Steps Per Second = 59.847
INFO:root:[Learner] Loss = 0.298 | Steps = 1807737 | Walltime

INFO:root:[Env Loop] Episode Length = 200 | Episode Return = 26.0 | Episodes = 54942 | Steps = 14467433 | Steps Per Second = 60.457
INFO:root:[Learner] Loss = 0.306 | Steps = 1808313 | Walltime = 240253.956
INFO:root:[Learner] Loss = 0.252 | Steps = 1808321 | Walltime = 240254.967
INFO:root:[Learner] Loss = 0.322 | Steps = 1808329 | Walltime = 240256.065
INFO:root:[Learner] Loss = 0.311 | Steps = 1808337 | Walltime = 240257.143
INFO:root:[Learner] Loss = 0.227 | Steps = 1808345 | Walltime = 240258.229
INFO:root:[Env Loop] Episode Length = 369 | Episode Return = 79.0 | Episodes = 54943 | Steps = 14467802 | Steps Per Second = 59.936
INFO:root:[Learner] Loss = 0.331 | Steps = 1808353 | Walltime = 240259.327
INFO:root:[Learner] Loss = 0.293 | Steps = 1808361 | Walltime = 240260.362
INFO:root:[Learner] Loss = 0.298 | Steps = 1808369 | Walltime = 240261.373
INFO:root:[Learner] Loss = 0.236 | Steps = 1808376 | Walltime = 240262.423
INFO:root:[Learner] Loss = 0.351 | Steps = 1808383 | Walltime

INFO:root:[Learner] Loss = 0.268 | Steps = 1808948 | Walltime = 240338.773
INFO:root:[Env Loop] Episode Length = 411 | Episode Return = 80.0 | Episodes = 54959 | Steps = 14472615 | Steps Per Second = 52.582
INFO:root:[Learner] Loss = 0.355 | Steps = 1808954 | Walltime = 240339.813
INFO:root:[Learner] Loss = 0.435 | Steps = 1808962 | Walltime = 240340.984
INFO:root:[Learner] Loss = 0.212 | Steps = 1808969 | Walltime = 240342.068
INFO:root:[Learner] Loss = 0.326 | Steps = 1808976 | Walltime = 240343.077
INFO:root:[Learner] Loss = 0.209 | Steps = 1808983 | Walltime = 240344.175
INFO:root:[Learner] Loss = 0.184 | Steps = 1808990 | Walltime = 240345.216
INFO:root:[Env Loop] Episode Length = 322 | Episode Return = 47.0 | Episodes = 54960 | Steps = 14472937 | Steps Per Second = 52.602
INFO:root:[Learner] Loss = 0.185 | Steps = 1808997 | Walltime = 240346.260
INFO:root:[Learner] Loss = 0.253 | Steps = 1809005 | Walltime = 240347.361
INFO:root:[Learner] Loss = 0.148 | Steps = 1809013 | Walltime

INFO:root:[Learner] Loss = 0.298 | Steps = 1809568 | Walltime = 240424.787
INFO:root:[Learner] Loss = 0.262 | Steps = 1809576 | Walltime = 240425.814
INFO:root:[Learner] Loss = 0.233 | Steps = 1809584 | Walltime = 240426.841
INFO:root:[Learner] Loss = 0.224 | Steps = 1809592 | Walltime = 240427.856
INFO:root:[Env Loop] Episode Length = 269 | Episode Return = 42.0 | Episodes = 54976 | Steps = 14477776 | Steps Per Second = 62.283
INFO:root:[Learner] Loss = 0.270 | Steps = 1809600 | Walltime = 240428.910
INFO:root:[Learner] Loss = 0.212 | Steps = 1809608 | Walltime = 240429.960
INFO:root:[Learner] Loss = 0.215 | Steps = 1809616 | Walltime = 240430.985
INFO:root:[Learner] Loss = 0.276 | Steps = 1809625 | Walltime = 240432.111
INFO:root:[Learner] Loss = 0.312 | Steps = 1809633 | Walltime = 240433.131
INFO:root:[Env Loop] Episode Length = 323 | Episode Return = 48.0 | Episodes = 54977 | Steps = 14478099 | Steps Per Second = 62.151
INFO:root:[Learner] Loss = 0.263 | Steps = 1809641 | Walltime

INFO:root:[Learner] Loss = 0.256 | Steps = 1810182 | Walltime = 240504.933
INFO:root:[Learner] Loss = 0.274 | Steps = 1810189 | Walltime = 240506.047
INFO:root:[Learner] Loss = 0.329 | Steps = 1810195 | Walltime = 240507.092
INFO:root:[Learner] Loss = 0.306 | Steps = 1810202 | Walltime = 240508.115
INFO:root:[Env Loop] Episode Length = 251 | Episode Return = 30.0 | Episodes = 54995 | Steps = 14482641 | Steps Per Second = 51.639
INFO:root:[Learner] Loss = 0.260 | Steps = 1810210 | Walltime = 240509.161
INFO:root:[Learner] Loss = 0.232 | Steps = 1810218 | Walltime = 240510.208
INFO:root:[Learner] Loss = 0.215 | Steps = 1810226 | Walltime = 240511.264
INFO:root:[Learner] Loss = 0.264 | Steps = 1810234 | Walltime = 240512.273
INFO:root:[Learner] Loss = 0.214 | Steps = 1810242 | Walltime = 240513.283
INFO:root:[Learner] Loss = 0.225 | Steps = 1810250 | Walltime = 240514.304
INFO:root:[Env Loop] Episode Length = 412 | Episode Return = 97.0 | Episodes = 54996 | Steps = 14483053 | Steps Per Se

In [26]:
env_loop.run(num_episodes=5000)

INFO:root:[Learner] Loss = 0.261 | Steps = 1810420 | Walltime = 240536.405
INFO:root:[Learner] Loss = 0.224 | Steps = 1810428 | Walltime = 240537.509
INFO:root:[Learner] Loss = 0.252 | Steps = 1810436 | Walltime = 240538.549
INFO:root:[Learner] Loss = 0.258 | Steps = 1810444 | Walltime = 240539.615
INFO:root:[Learner] Loss = 0.213 | Steps = 1810452 | Walltime = 240540.639
INFO:root:[Env Loop] Episode Length = 316 | Episode Return = 54.0 | Episodes = 55001 | Steps = 14484613 | Steps Per Second = 60.538
INFO:root:[Learner] Loss = 0.179 | Steps = 1810460 | Walltime = 240541.776
INFO:root:[Learner] Loss = 0.305 | Steps = 1810468 | Walltime = 240542.797
INFO:root:[Learner] Loss = 0.304 | Steps = 1810476 | Walltime = 240543.802
INFO:root:[Env Loop] Episode Length = 253 | Episode Return = 30.0 | Episodes = 55002 | Steps = 14484866 | Steps Per Second = 61.909
INFO:root:[Learner] Loss = 0.342 | Steps = 1810485 | Walltime = 240544.961
INFO:root:[Learner] Loss = 0.279 | Steps = 1810493 | Walltime

INFO:root:[Learner] Loss = 0.181 | Steps = 1811060 | Walltime = 240620.885
INFO:root:[Learner] Loss = 0.311 | Steps = 1811068 | Walltime = 240621.894
INFO:root:[Learner] Loss = 0.351 | Steps = 1811076 | Walltime = 240622.903
INFO:root:[Learner] Loss = 0.248 | Steps = 1811084 | Walltime = 240623.935
INFO:root:[Learner] Loss = 0.221 | Steps = 1811092 | Walltime = 240624.946
INFO:root:[Learner] Loss = 0.267 | Steps = 1811100 | Walltime = 240625.956
INFO:root:[Env Loop] Episode Length = 375 | Episode Return = 72.0 | Episodes = 55018 | Steps = 14489803 | Steps Per Second = 62.785
INFO:root:[Learner] Loss = 0.301 | Steps = 1811108 | Walltime = 240626.974
INFO:root:[Learner] Loss = 0.236 | Steps = 1811116 | Walltime = 240627.996
INFO:root:[Learner] Loss = 0.384 | Steps = 1811124 | Walltime = 240629.026
INFO:root:[Env Loop] Episode Length = 181 | Episode Return = 20.0 | Episodes = 55019 | Steps = 14489984 | Steps Per Second = 62.030
INFO:root:[Learner] Loss = 0.289 | Steps = 1811132 | Walltime

INFO:root:[Learner] Loss = 0.225 | Steps = 1811708 | Walltime = 240705.495
INFO:root:[Learner] Loss = 0.354 | Steps = 1811716 | Walltime = 240706.535
INFO:root:[Env Loop] Episode Length = 264 | Episode Return = 36.0 | Episodes = 55035 | Steps = 14494728 | Steps Per Second = 61.046
INFO:root:[Learner] Loss = 0.278 | Steps = 1811724 | Walltime = 240707.556
INFO:root:[Learner] Loss = 0.343 | Steps = 1811732 | Walltime = 240708.573
INFO:root:[Learner] Loss = 0.250 | Steps = 1811741 | Walltime = 240709.711
INFO:root:[Env Loop] Episode Length = 233 | Episode Return = 36.0 | Episodes = 55036 | Steps = 14494961 | Steps Per Second = 62.669
INFO:root:[Learner] Loss = 0.328 | Steps = 1811749 | Walltime = 240710.807
INFO:root:[Learner] Loss = 0.252 | Steps = 1811757 | Walltime = 240711.810
INFO:root:[Learner] Loss = 0.241 | Steps = 1811766 | Walltime = 240712.935
INFO:root:[Learner] Loss = 0.295 | Steps = 1811774 | Walltime = 240713.949
INFO:root:[Env Loop] Episode Length = 225 | Episode Return = 

INFO:root:[Learner] Loss = 0.243 | Steps = 1812294 | Walltime = 240780.617
INFO:root:[Learner] Loss = 0.280 | Steps = 1812302 | Walltime = 240781.630
INFO:root:[Env Loop] Episode Length = 273 | Episode Return = 32.0 | Episodes = 55057 | Steps = 14499425 | Steps Per Second = 60.943
INFO:root:[Learner] Loss = 0.237 | Steps = 1812310 | Walltime = 240782.691
INFO:root:[Learner] Loss = 0.341 | Steps = 1812318 | Walltime = 240783.707
INFO:root:[Env Loop] Episode Length = 182 | Episode Return = 24.0 | Episodes = 55058 | Steps = 14499607 | Steps Per Second = 64.322
INFO:root:[Learner] Loss = 0.250 | Steps = 1812327 | Walltime = 240784.848
INFO:root:[Learner] Loss = 0.221 | Steps = 1812336 | Walltime = 240785.945
INFO:root:[Learner] Loss = 0.231 | Steps = 1812344 | Walltime = 240786.965
INFO:root:[Env Loop] Episode Length = 163 | Episode Return = 15.0 | Episodes = 55059 | Steps = 14499770 | Steps Per Second = 62.912
INFO:root:[Learner] Loss = 0.297 | Steps = 1812352 | Walltime = 240787.979
INFO

INFO:root:[Learner] Loss = 0.311 | Steps = 1812912 | Walltime = 240861.799
INFO:root:[Learner] Loss = 0.233 | Steps = 1812920 | Walltime = 240862.834
INFO:root:[Learner] Loss = 0.240 | Steps = 1812928 | Walltime = 240863.900
INFO:root:[Learner] Loss = 0.217 | Steps = 1812936 | Walltime = 240864.914
INFO:root:[Learner] Loss = 0.229 | Steps = 1812944 | Walltime = 240865.954
INFO:root:[Env Loop] Episode Length = 331 | Episode Return = 53.0 | Episodes = 55076 | Steps = 14504557 | Steps Per Second = 62.042
INFO:root:[Learner] Loss = 0.236 | Steps = 1812952 | Walltime = 240867.048
INFO:root:[Learner] Loss = 0.228 | Steps = 1812960 | Walltime = 240868.078
INFO:root:[Learner] Loss = 0.302 | Steps = 1812969 | Walltime = 240869.177
INFO:root:[Env Loop] Episode Length = 244 | Episode Return = 25.0 | Episodes = 55077 | Steps = 14504801 | Steps Per Second = 62.474
INFO:root:[Learner] Loss = 0.213 | Steps = 1812977 | Walltime = 240870.202
INFO:root:[Learner] Loss = 0.313 | Steps = 1812985 | Walltime

...

INFO:root:[Learner] Loss = 0.212 | Steps = 1989332 | Walltime = 264267.143
INFO:root:[Learner] Loss = 0.271 | Steps = 1989340 | Walltime = 264268.227
INFO:root:[Learner] Loss = 0.312 | Steps = 1989348 | Walltime = 264269.276
INFO:root:[Env Loop] Episode Length = 276 | Episode Return = 34.0 | Episodes = 59928 | Steps = 15915821 | Steps Per Second = 59.833
INFO:root:[Learner] Loss = 0.287 | Steps = 1989356 | Walltime = 264270.333
INFO:root:[Learner] Loss = 0.279 | Steps = 1989364 | Walltime = 264271.414
INFO:root:[Learner] Loss = 0.285 | Steps = 1989372 | Walltime = 264272.506
INFO:root:[Learner] Loss = 0.236 | Steps = 1989380 | Walltime = 264273.586
INFO:root:[Learner] Loss = 0.226 | Steps = 1989388 | Walltime = 264274.689
INFO:root:[Env Loop] Episode Length = 277 | Episode Return = 45.0 | Episodes = 59929 | Steps = 15916098 | Steps Per Second = 58.498
INFO:root:[Learner] Loss = 0.297 | Steps = 1989396 | Walltime = 264275.797
INFO:root:[Learner] Loss = 0.249 | Steps = 1989404 | Walltime

INFO:root:[Learner] Loss = 0.312 | Steps = 1989983 | Walltime = 264351.860
INFO:root:[Env Loop] Episode Length = 309 | Episode Return = 32.0 | Episodes = 59945 | Steps = 15920879 | Steps Per Second = 59.914
INFO:root:[Learner] Loss = 0.214 | Steps = 1989990 | Walltime = 264352.943
INFO:root:[Learner] Loss = 0.204 | Steps = 1989997 | Walltime = 264353.970
INFO:root:[Learner] Loss = 0.225 | Steps = 1990004 | Walltime = 264355.055
INFO:root:[Learner] Loss = 0.204 | Steps = 1990011 | Walltime = 264356.076
INFO:root:[Learner] Loss = 0.217 | Steps = 1990019 | Walltime = 264357.193
INFO:root:[Learner] Loss = 0.320 | Steps = 1990027 | Walltime = 264358.269
INFO:root:[Learner] Loss = 0.301 | Steps = 1990035 | Walltime = 264359.273
INFO:root:[Env Loop] Episode Length = 414 | Episode Return = 97.0 | Episodes = 59946 | Steps = 15921293 | Steps Per Second = 56.488
INFO:root:[Learner] Loss = 0.296 | Steps = 1990043 | Walltime = 264360.364
INFO:root:[Learner] Loss = 0.235 | Steps = 1990052 | Walltime

INFO:root:[Learner] Loss = 0.293 | Steps = 1990657 | Walltime = 264439.469
INFO:root:[Learner] Loss = 0.264 | Steps = 1990666 | Walltime = 264440.564
INFO:root:[Learner] Loss = 0.176 | Steps = 1990675 | Walltime = 264441.677
INFO:root:[Learner] Loss = 0.289 | Steps = 1990684 | Walltime = 264442.802
INFO:root:[Env Loop] Episode Length = 572 | Episode Return = 65.0 | Episodes = 59960 | Steps = 15926520 | Steps Per Second = 62.971
INFO:root:[Learner] Loss = 0.206 | Steps = 1990692 | Walltime = 264443.825
INFO:root:[Learner] Loss = 0.206 | Steps = 1990700 | Walltime = 264444.871
INFO:root:[Learner] Loss = 0.185 | Steps = 1990708 | Walltime = 264445.924
INFO:root:[Learner] Loss = 0.185 | Steps = 1990716 | Walltime = 264446.951
INFO:root:[Learner] Loss = 0.294 | Steps = 1990724 | Walltime = 264447.975
INFO:root:[Learner] Loss = 0.201 | Steps = 1990732 | Walltime = 264449.058
INFO:root:[Env Loop] Episode Length = 366 | Episode Return = 33.0 | Episodes = 59961 | Steps = 15926886 | Steps Per Se

INFO:root:[Learner] Loss = 0.364 | Steps = 1991365 | Walltime = 264531.266
INFO:root:[Learner] Loss = 0.259 | Steps = 1991373 | Walltime = 264532.329
INFO:root:[Learner] Loss = 0.271 | Steps = 1991381 | Walltime = 264533.423
INFO:root:[Env Loop] Episode Length = 425 | Episode Return = 30.0 | Episodes = 59973 | Steps = 15932085 | Steps Per Second = 61.140
INFO:root:[Learner] Loss = 0.313 | Steps = 1991389 | Walltime = 264534.501
INFO:root:[Learner] Loss = 0.318 | Steps = 1991397 | Walltime = 264535.520
INFO:root:[Learner] Loss = 0.286 | Steps = 1991405 | Walltime = 264536.590
INFO:root:[Learner] Loss = 0.239 | Steps = 1991413 | Walltime = 264537.665
INFO:root:[Learner] Loss = 0.324 | Steps = 1991421 | Walltime = 264538.668
INFO:root:[Learner] Loss = 0.380 | Steps = 1991429 | Walltime = 264539.725
INFO:root:[Env Loop] Episode Length = 395 | Episode Return = 81.0 | Episodes = 59974 | Steps = 15932480 | Steps Per Second = 60.937
INFO:root:[Learner] Loss = 0.236 | Steps = 1991437 | Walltime

INFO:root:[Learner] Loss = 0.290 | Steps = 1992039 | Walltime = 264618.372
INFO:root:[Learner] Loss = 0.285 | Steps = 1992047 | Walltime = 264619.439
INFO:root:[Learner] Loss = 0.269 | Steps = 1992055 | Walltime = 264620.478
INFO:root:[Env Loop] Episode Length = 419 | Episode Return = 71.0 | Episodes = 59988 | Steps = 15937450 | Steps Per Second = 59.769
INFO:root:[Learner] Loss = 0.324 | Steps = 1992063 | Walltime = 264621.544
INFO:root:[Learner] Loss = 0.220 | Steps = 1992071 | Walltime = 264622.587
INFO:root:[Learner] Loss = 0.323 | Steps = 1992079 | Walltime = 264623.634
INFO:root:[Env Loop] Episode Length = 221 | Episode Return = 22.0 | Episodes = 59989 | Steps = 15937671 | Steps Per Second = 61.407
INFO:root:[Learner] Loss = 0.215 | Steps = 1992087 | Walltime = 264624.729
INFO:root:[Learner] Loss = 0.206 | Steps = 1992095 | Walltime = 264625.791
INFO:root:[Learner] Loss = 0.230 | Steps = 1992103 | Walltime = 264626.880
INFO:root:[Learner] Loss = 0.323 | Steps = 1992111 | Walltime

In [20]:
env_loop.run(num_episodes=5000)

INFO:root:[Learner] Loss = 0.255 | Steps = 1101885 | Walltime = 146347.247
INFO:root:[Learner] Loss = 0.333 | Steps = 1101893 | Walltime = 146348.303
INFO:root:[Learner] Loss = 0.332 | Steps = 1101902 | Walltime = 146349.416
INFO:root:[Learner] Loss = 0.205 | Steps = 1101911 | Walltime = 146350.523
INFO:root:[Env Loop] Episode Length = 275 | Episode Return = 42.0 | Episodes = 35001 | Steps = 8816328 | Steps Per Second = 61.874
INFO:root:[Learner] Loss = 0.268 | Steps = 1101919 | Walltime = 146351.606
INFO:root:[Learner] Loss = 0.301 | Steps = 1101927 | Walltime = 146352.672
INFO:root:[Learner] Loss = 0.266 | Steps = 1101935 | Walltime = 146353.705
INFO:root:[Env Loop] Episode Length = 173 | Episode Return = 16.0 | Episodes = 35002 | Steps = 8816501 | Steps Per Second = 60.770
INFO:root:[Learner] Loss = 0.261 | Steps = 1101943 | Walltime = 146354.780
INFO:root:[Learner] Loss = 0.285 | Steps = 1101951 | Walltime = 146355.843
INFO:root:[Learner] Loss = 0.278 | Steps = 1101959 | Walltime =

INFO:root:[Learner] Loss = 0.321 | Steps = 1102481 | Walltime = 146427.096
INFO:root:[Learner] Loss = 0.277 | Steps = 1102489 | Walltime = 146428.137
INFO:root:[Learner] Loss = 0.260 | Steps = 1102497 | Walltime = 146429.186
INFO:root:[Learner] Loss = 0.221 | Steps = 1102505 | Walltime = 146430.272
INFO:root:[Env Loop] Episode Length = 214 | Episode Return = 19.0 | Episodes = 35021 | Steps = 8821046 | Steps Per Second = 60.050
INFO:root:[Learner] Loss = 0.247 | Steps = 1102513 | Walltime = 146431.395
INFO:root:[Learner] Loss = 0.245 | Steps = 1102521 | Walltime = 146432.429
INFO:root:[Learner] Loss = 0.292 | Steps = 1102530 | Walltime = 146433.549
INFO:root:[Learner] Loss = 0.274 | Steps = 1102539 | Walltime = 146434.658
INFO:root:[Env Loop] Episode Length = 275 | Episode Return = 34.0 | Episodes = 35022 | Steps = 8821321 | Steps Per Second = 62.040
INFO:root:[Learner] Loss = 0.203 | Steps = 1102547 | Walltime = 146435.713
INFO:root:[Learner] Loss = 0.215 | Steps = 1102555 | Walltime =

INFO:root:[Learner] Loss = 0.393 | Steps = 1103103 | Walltime = 146507.905
INFO:root:[Learner] Loss = 0.228 | Steps = 1103112 | Walltime = 146509.020
INFO:root:[Env Loop] Episode Length = 357 | Episode Return = 67.0 | Episodes = 35040 | Steps = 8825935 | Steps Per Second = 63.053
INFO:root:[Learner] Loss = 0.248 | Steps = 1103120 | Walltime = 146510.076
INFO:root:[Learner] Loss = 0.287 | Steps = 1103128 | Walltime = 146511.091
INFO:root:[Learner] Loss = 0.283 | Steps = 1103136 | Walltime = 146512.101
INFO:root:[Env Loop] Episode Length = 187 | Episode Return = 21.0 | Episodes = 35041 | Steps = 8826122 | Steps Per Second = 62.167
INFO:root:[Learner] Loss = 0.325 | Steps = 1103144 | Walltime = 146513.171
INFO:root:[Learner] Loss = 0.281 | Steps = 1103153 | Walltime = 146514.294
INFO:root:[Learner] Loss = 0.266 | Steps = 1103161 | Walltime = 146515.319
INFO:root:[Env Loop] Episode Length = 210 | Episode Return = 27.0 | Episodes = 35042 | Steps = 8826332 | Steps Per Second = 62.725
INFO:ro

INFO:root:[Env Loop] Episode Length = 170 | Episode Return = 26.0 | Episodes = 35059 | Steps = 8830696 | Steps Per Second = 60.535
INFO:root:[Learner] Loss = 0.207 | Steps = 1103717 | Walltime = 146589.805
INFO:root:[Learner] Loss = 0.265 | Steps = 1103725 | Walltime = 146590.843
INFO:root:[Env Loop] Episode Length = 154 | Episode Return = 14.0 | Episodes = 35060 | Steps = 8830850 | Steps Per Second = 59.633
INFO:root:[Learner] Loss = 0.283 | Steps = 1103733 | Walltime = 146591.937
INFO:root:[Learner] Loss = 0.178 | Steps = 1103741 | Walltime = 146592.974
INFO:root:[Learner] Loss = 0.357 | Steps = 1103749 | Walltime = 146594.037
INFO:root:[Learner] Loss = 0.299 | Steps = 1103757 | Walltime = 146595.167
INFO:root:[Env Loop] Episode Length = 243 | Episode Return = 28.0 | Episodes = 35061 | Steps = 8831093 | Steps Per Second = 60.263
INFO:root:[Learner] Loss = 0.221 | Steps = 1103765 | Walltime = 146596.190
INFO:root:[Learner] Loss = 0.259 | Steps = 1103774 | Walltime = 146597.303
INFO:ro

INFO:root:[Learner] Loss = 0.289 | Steps = 1104346 | Walltime = 146672.004
INFO:root:[Env Loop] Episode Length = 172 | Episode Return = 22.0 | Episodes = 35077 | Steps = 8835796 | Steps Per Second = 61.629
INFO:root:[Learner] Loss = 0.297 | Steps = 1104354 | Walltime = 146673.053
INFO:root:[Learner] Loss = 0.368 | Steps = 1104362 | Walltime = 146674.056
INFO:root:[Learner] Loss = 0.304 | Steps = 1104370 | Walltime = 146675.116
INFO:root:[Learner] Loss = 0.306 | Steps = 1104378 | Walltime = 146676.130
INFO:root:[Learner] Loss = 0.336 | Steps = 1104386 | Walltime = 146677.158
INFO:root:[Env Loop] Episode Length = 312 | Episode Return = 55.0 | Episodes = 35078 | Steps = 8836108 | Steps Per Second = 62.288
INFO:root:[Learner] Loss = 0.232 | Steps = 1104394 | Walltime = 146678.179
INFO:root:[Learner] Loss = 0.222 | Steps = 1104402 | Walltime = 146679.201
INFO:root:[Learner] Loss = 0.321 | Steps = 1104410 | Walltime = 146680.247
INFO:root:[Learner] Loss = 0.330 | Steps = 1104419 | Walltime =

...

INFO:root:[Learner] Loss = 0.335 | Steps = 1276401 | Walltime = 169316.580
INFO:root:[Learner] Loss = 0.214 | Steps = 1276409 | Walltime = 169317.697
INFO:root:[Learner] Loss = 0.242 | Steps = 1276417 | Walltime = 169318.794
INFO:root:[Learner] Loss = 0.298 | Steps = 1276425 | Walltime = 169319.864
INFO:root:[Env Loop] Episode Length = 337 | Episode Return = 47.0 | Episodes = 39927 | Steps = 10212439 | Steps Per Second = 59.691
INFO:root:[Learner] Loss = 0.240 | Steps = 1276433 | Walltime = 169320.938
INFO:root:[Learner] Loss = 0.318 | Steps = 1276441 | Walltime = 169322.016
INFO:root:[Learner] Loss = 0.322 | Steps = 1276449 | Walltime = 169323.110
INFO:root:[Learner] Loss = 0.337 | Steps = 1276457 | Walltime = 169324.215
INFO:root:[Env Loop] Episode Length = 259 | Episode Return = 40.0 | Episodes = 39928 | Steps = 10212698 | Steps Per Second = 57.996
INFO:root:[Learner] Loss = 0.137 | Steps = 1276464 | Walltime = 169325.223
INFO:root:[Learner] Loss = 0.225 | Steps = 1276472 | Walltime

INFO:root:[Learner] Loss = 0.319 | Steps = 1277020 | Walltime = 169399.633
INFO:root:[Learner] Loss = 0.251 | Steps = 1277028 | Walltime = 169400.672
INFO:root:[Learner] Loss = 0.322 | Steps = 1277036 | Walltime = 169401.700
INFO:root:[Learner] Loss = 0.143 | Steps = 1277044 | Walltime = 169402.707
INFO:root:[Env Loop] Episode Length = 241 | Episode Return = 28.0 | Episodes = 39945 | Steps = 10217383 | Steps Per Second = 62.150
INFO:root:[Learner] Loss = 0.331 | Steps = 1277052 | Walltime = 169403.762
INFO:root:[Learner] Loss = 0.261 | Steps = 1277060 | Walltime = 169404.810
INFO:root:[Learner] Loss = 0.263 | Steps = 1277068 | Walltime = 169405.888
INFO:root:[Learner] Loss = 0.274 | Steps = 1277076 | Walltime = 169406.947
INFO:root:[Learner] Loss = 0.253 | Steps = 1277084 | Walltime = 169407.958
INFO:root:[Learner] Loss = 0.176 | Steps = 1277093 | Walltime = 169409.065
INFO:root:[Env Loop] Episode Length = 362 | Episode Return = 75.0 | Episodes = 39946 | Steps = 10217745 | Steps Per Se

INFO:root:[Learner] Loss = 0.326 | Steps = 1277633 | Walltime = 169481.676
INFO:root:[Learner] Loss = 0.249 | Steps = 1277641 | Walltime = 169482.718
INFO:root:[Learner] Loss = 0.268 | Steps = 1277649 | Walltime = 169483.737
INFO:root:[Learner] Loss = 0.173 | Steps = 1277657 | Walltime = 169484.785
INFO:root:[Env Loop] Episode Length = 254 | Episode Return = 32.0 | Episodes = 39964 | Steps = 10222291 | Steps Per Second = 61.163
INFO:root:[Learner] Loss = 0.287 | Steps = 1277665 | Walltime = 169485.840
INFO:root:[Learner] Loss = 0.218 | Steps = 1277673 | Walltime = 169486.894
INFO:root:[Learner] Loss = 0.229 | Steps = 1277681 | Walltime = 169487.942
INFO:root:[Learner] Loss = 0.265 | Steps = 1277689 | Walltime = 169488.981
INFO:root:[Learner] Loss = 0.250 | Steps = 1277697 | Walltime = 169490.021
INFO:root:[Env Loop] Episode Length = 289 | Episode Return = 37.0 | Episodes = 39965 | Steps = 10222580 | Steps Per Second = 60.756
INFO:root:[Learner] Loss = 0.218 | Steps = 1277705 | Walltime

INFO:root:[Learner] Loss = 0.298 | Steps = 1278260 | Walltime = 169564.129
INFO:root:[Env Loop] Episode Length = 155 | Episode Return = 14.0 | Episodes = 39982 | Steps = 10227124 | Steps Per Second = 60.416
INFO:root:[Learner] Loss = 0.198 | Steps = 1278268 | Walltime = 169565.163
INFO:root:[Learner] Loss = 0.266 | Steps = 1278276 | Walltime = 169566.225
INFO:root:[Learner] Loss = 0.321 | Steps = 1278283 | Walltime = 169567.289
INFO:root:[Learner] Loss = 0.231 | Steps = 1278291 | Walltime = 169568.453
INFO:root:[Env Loop] Episode Length = 247 | Episode Return = 33.0 | Episodes = 39983 | Steps = 10227371 | Steps Per Second = 57.333
INFO:root:[Learner] Loss = 0.292 | Steps = 1278299 | Walltime = 169569.500
INFO:root:[Learner] Loss = 0.261 | Steps = 1278307 | Walltime = 169570.571
INFO:root:[Learner] Loss = 0.367 | Steps = 1278316 | Walltime = 169571.706
INFO:root:[Learner] Loss = 0.211 | Steps = 1278324 | Walltime = 169572.755
INFO:root:[Learner] Loss = 0.226 | Steps = 1278332 | Walltime

INFO:root:[Learner] Loss = 0.206 | Steps = 1278888 | Walltime = 169646.932
INFO:root:[Learner] Loss = 0.284 | Steps = 1278896 | Walltime = 169648.021
INFO:root:[Env Loop] Episode Length = 263 | Episode Return = 30.0 | Episodes = 40000 | Steps = 10232191 | Steps Per Second = 60.668


In [ ]:
agent

In [ ]:
from tensorflow.saved_model import load

In [ ]:
agent = load('/home/hayato/acme/b8ca9590-d77d-11eb-b169-332db766104b/checkpoints/dqn_learner')

In [ ]:
# agent.save('pong_model')
from acme.tf.savers import Checkpointer, Snapshotter

In [ ]:
checkpointer = Checkpointer(objects_to_save={'model': network})

In [ ]:
checkpointer._checkpoint_dir = '/home/hayato/acme/b8ca9590-d77d-11eb-b169-332db766104b/checkpoints/dqn_learner'

In [ ]:
agent._checkpointer

In [ ]:
from tensorflow.train import Checkpoint

In [ ]:
checkpointer._checkpoint_manager._latest_checkpoint = '/home/hayato/acme/b8ca9590-d77d-11eb-b169-332db766104b/checkpoints/dqn_learner'

In [ ]:
# checkpointer = Checkpointer(objects_to_save={'model': agent})
snapshot = Snapshotter(objects_to_save={"model": network})

In [ ]:
snapshot.save()